<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"></ul></div>

In [1]:
import requests 
from bs4 import BeautifulSoup 
import pandas as pd
from pandas import ExcelWriter 
import openpyxl 
import lxml 
import re
import json
from datetime import datetime, timedelta
import time
import math
import ast
import numpy as np


from tqdm.auto import tqdm

In [2]:
#Создаю функцию выгрузки количества страниц
headers = { 
    "Accept": "*/*", 
    "Accept-Language": "ru-RU,ru;q=0.8,en-US;q=0.5,en;q=0.3", 
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:84.0) Gecko/20100101 Firefox/84.0", 
}

def get_pages(url, params=None):
    m=1
    while m>0:
        try:
            response = requests.get(url, headers=headers, params=params) 
            html = response.text
            soup = BeautifulSoup(html, 'lxml')
            good_count = soup.find('span', class_='goods-count').get_text(strip=True).replace("\xa0", '').split()[0]
            pages = int(good_count) // 100 + 1
            m=-10
        except:
            print(url)
            m+=1
    return pages


html = (requests.get(q, headers=headers, params={'sort': 'popular','page': 3})).text
soup = BeautifulSoup(html, 'html.parser') 
#print(soup)
#items = soup.find_all('div', class_="product-card") 

In [10]:
#Список категорий
categories = {
'Женщинам':
['zhenshchinam/odezhda',
'zhenshchinam/bolshie-razmery',
'budushchie-mamy',
'zhenshchinam/bele',
'zhenshchinam/dlya-vysokih',
'zhenshchinam/dlya-nevysokih',
'zhenshchinam/odezhda/odezhda-dlya-doma',
'zhenshchinam/ofis',
'zhenshchinam/plyazhnaya-moda',
'zhenshchinam/religioznaya',
'svadba',
'zhenshchinam/spetsodezhda',
'podarki/zhenshchinam'],
'Мужчинам':
['muzhchinam/odezhda',
'muzhchinam/bolshie-razmery' ,  
'muzhchinam/dlya-vysokih',
'muzhchinam/dlya-nevysokih',
'muzhchinam/bele',
'muzhchinam/odezhda/odezhda-dlya-doma',
'muzhchinam/ofis',
'muzhchinam/plyazhnay-odezhda',
'muzhchinam/religioznaya',
'muzhchinam/svadba',
'muzhchinam/spetsodezhda',
'podarki/muzhchinam'],
'Детям':
['detyam/dlya-devochek',
'detyam/odezhda/dlya-malchikov',
'detyam/odezhda/dlya-novorozhdennyh',
'elektronika/detskaya-elektronika',
'detyam/konstruktory',
'sport/dlya-detey/detskiy-transport',
'detyam/detskoe-pitanie',
'detyam/religioznaya',
'detyam/tovary-dlya-malysha',
'detyam/tovary-dlya-malysha/podguzniki/podguzniki-detskie',
'podarki/detyam'],
'Обувь':
['obuv/detskaya',
'obuv/dlya-novorozhdennyh',
'obuv/zhenskaya',
'obuv/muzhskaya',
'obuv/ortopedicheskaya-obuv',
'obuv/aksessuary-dlya-obuvi'],
'Аксессуары':
['aksessuary/aksessuary-dlya-volos',
'aksessuary/dekor-dlya-odezhdy',
'aksessuary/bizhuteriya',
'aksessuary/veera',
'aksessuary/galstuki-i-babochki',
'aksessuary/golovnye-ubory',
'aksessuary/zerkaltsa',
'aksessuary/zonty',
'aksessuary/koshelki-i-kreditnitsy',
'aksessuary/maski-dlya-sna',
'aksessuary/nosovye-platki',
'aksessuary/ochki-i-futlyary',
'aksessuary/perchatki-i-varezhki',
'aksessuary/platki-i-sharfy',
'aksessuary/religioznye',
'aksessuary/remni-i-poyasa',
'aksessuary/sumki-i-ryukzaki',
'aksessuary/chasy-i-remeshki',
'muzhchinam/aksessuary/chemodany-i-dorozhnye-sumki',
'elektronika/avtoelektronika'],
'Электроника':
['elektronika/igry-i-razvlecheniya/aksessuary/garnitury',
'elektronika/detskaya-elektronika',
'elektronika/razvlecheniya-i-gadzhety/igrovye-konsoli',
'elektronika/kabeli-i-zaryadnye-ustroystva',
'elektronika/muzyka-i-video',
'elektronika/noutbuki-periferiya',
'elektronika/ofisnaya-tehnika',
'elektronika/razvlecheniya-i-gadzhety',
'elektronika/setevoe-oborudovanie',
'elektronika/bezopasnost-doma',
'elektronika/smart-chasy',
'elektronika/tv-audio-foto-video-tehnika',
'elektronika/torgovoe-oborudovanie',
'elektronika/umnyy-dom',
'sport/elektrotransport-i-aksessuary',
'elektronika/tehnika-dlya-doma/uvlazhniteli-i-vozduhootchistiteli',
'elektronika/krasota-i-zdorove',
'bytovaya-tehnika/sadovaya-tehnika',
'elektronika/tehnika-dlya-doma',
'elektronika/tehnika-dlya-kuhni',
'bytovaya-tehnika/krupnaya-bytovaya-tehnika'],
'Книги':
['knigi/detyam-i-roditelyam',
'knigi/uchebnaya-literatura',
'knigi/entsiklopedii',
'knigi/hudozhestvennaya-literatura',
'knigi/zhurnaly',
'knigi/knigi-rodoslovnye',
'knigi/kollektsionnye-izdaniya',
'knigi/bukinistika',
'knigi-i-diski/kantstovary/bloknoty-tvorcheskie',
'knigi-i-diski/multimedia',
'knigi/audioknigi',
'knigi/inostrannye-knigi'],
'Спорт':
['sport/vidy-sporta/fitnes/yoga',
'sport/vidy-sporta/velosport',
'sport/vidy-sporta/yoga',
'sport/vidy-sporta/ohota-i-rybolovstvo',
'sport/vidy-sporta/roliki-samokaty',
'sport/vidy-sporta/turizm-kemping',
'sport/vidy-sporta/beg/hodba',
'sport/vidy-sporta/komandnye-vidy-sporta',
'sport/vidy-sporta/plavanie',
'sport/vidy-sporta/zimnie-vidy-sporta',
'sport/podderzhka-i-vosstanovlenie',
'sport/sportivnoe-pitanie',
'sport/vidy-sporta/badminton/tennis',
'sport/bilyard/darts',
'sport/vidy-sporta/edinoborstva',
'sport/konniy-sport',
'sport/vidy-sporta/motosport',
'sport/vidy-sporta/parusnyisport',
'sport/vidy-sporta/skalolazanie/alpinizm',
'sport/vidy-sporta/straykbol',
'sport/vidy-sporta/tantsy/gimnastika',
'sport/dlya-detey',
'sport/dlya-zhenshchin',
'sport/dlya-muzhchin',
'sport/sportivnaya-obuv',
'sport/elektronika'],
#'Школа':
#['detyam/shkola/odezhda-dlya-devochek',
#'detyam/shkola/odezhda-dlya-malchikov',
#'shkola/banty',
#'detyam/shkola/galstuki-i-babochki',
#'aksessuary/sumki-i-ryukzaki/ryukzaki-i-rantsy/doshkolnye-ryukzaki',
#'shkola/lenty-vypusknika',
#'detyam/shkola/obuv-dlya-devochek',
#'detyam/shkola/obuv-dlya-malchikov',
#'detyam/shkola/rantsy',
#'detyam/shkola/sport',
#'detyam/shkola/uchebnaya-literatura',
#'detyam/shkola/shkolnye-prinadlezhnosti',
#'detyam/shkola/shkolnye-ryukzaki'],
'Красота':
['krasota/aksessuary',
'krasota/volosy',
'krasota/aptechnaya-kosmetika',
'krasota/detskaya-dekorativnaya-kosmetika',
'krasota/zashchita-ot-solntsa',
'krasota/dlya-mam-i-malyshey',
'krasota/izrailskaya-kosmetika',
'krasota/instrumenty-dlya-parikmaherov',
'krasota/koreyskie-brendy',
'elektronika/kosmeticheskie-apparaty',
'krasota/makiyazh',
'krasota/muzhskaya-liniya',
'krasota/nogti',
'krasota/organicheskaya-kosmetika',
'krasota/parfyumeriya',
'krasota/podarochnye-nabory',
'krasota/professionalnaya-kosmetika/krasota',
'krasota/sredstva-lichnoy-gigieny',
'krasota/uhod-za-zubami',
'krasota/uhod-za-kozhey'],
'Игрушки':
['igrushki/antistress',
'igrushki/dlya-malyshey',
'igrushki/dlya-pesochnitsy',
'igrushki/igrovye-kompleksy',
'igrushki/igrovye-nabory',
'igrushki/igrushechnoe-oruzhie',
'igrushki/igrushechniy-transport',
'igrushki/igrushki-dlya-vannoy',
'igrushki/interaktivnye',
'igrushki/kineticheskiy-pesok',
'igrushki/konstruktory',
'igrushki/konstruktory-lego',
'igrushki/kukly-i-aksessuary',
'igrushki/muzykalnye-instrumenty',
'igrushki/mylnye-puzyri',
'igrushki/myagkie-igrushki',
'igrushki/opyty',
'igrushki/nastolnye-igry',
'igrushki/radioupravlyaemye-igrushki/radioupravlyaemye-igrushki',
'igrushki/razvivayushchie-igrushki',
'igrushki/sbornye-modeli',
'igrushki/sportivnye-igry',
'igrushki/syuzhetno-rolevye-igry',
'igrushki/tvorchestvo-i-rukodelie',
'igrushki/figurki-i-roboty'],
'Продукты':
['produkty/vkusnye-podarki',
'produkty-pitaniya/chay-kofe',
'pitanie/sladosti',
'pitanie/bakaleya',
'pitanie/detskoe-pitanie',
'produkty/dobavki-pishchevye',
'pitanie/zdorovoe-pitanie',
'produkty/myasnaya-produktsiya',
'pitanie/chay-kofe/moloko-i-slivki',
'pitanie/napitki',
'pitanie/sneki',
'produkty/zamorozhennaya-produktsiya',
'produkty/frukty',
'produkty/ovoshchi'],
'Дача':
['dachniy-sezon/basseyny',
'dom/sad-i-dacha/gorshki-opory-i-vse-dlya-rassady',
'dom/sad-i-dacha/grili-mangaly-i-barbekyu',
'dom/dachniy-sezon/dachnye-umyvalniki-dushi-i-tualety',
'dom/dachniy-sezon/moyki-vysokogo-davleniya-i-aksessuary',
'dom/dachniy-sezon/poliv-i-vodosnabzhenie',
'dom/dachniy-sezon/rasteniya-semena-i-grunty',
'dom/dachniy-sezon/sadovaya-mebel',
'dom/sad-i-dacha/sadovaya-tehnika',
'dom/dachniy-sezon/sadoviy-dekor',
'dom/dachniy-sezon/sadoviy-instrument',
'dom/dachniy-sezon/teplitsy-parniki-ukryvnoy-material',
'dom-i-dacha/tovary-dlya-bani',
'dom/dachniy-sezon/tovary-dlya-kempinga-piknika-i-otdyha',
'dom/dachniy-sezon/udobreniya-himikaty-i-sredstva-zashchity'],
'Здоровье':
['dom-i-dacha/zdorove/vitaminy-i-bady',
'dom-i-dacha/zdorove/lekarstvennye-preparaty/antibakterialnye-i-antisepticheskie-preparaty',
'dom-i-dacha/zdorove/kontratseptivy-i-lubrikanty',
'zdorove/lechebnoe-pitanie-',
'aksessuary/golovnye-ubory/maski-vetrozashchitnye',
'dom-i-dacha/zdorove/meditsinskie-izdeliya-i-pribory',
'dom-i-dacha/zdorove/meditsinskie-izdeliya-i-pribory/meditsinskie-pribory',
'zdorove/ozdorovlenie',
'dom-i-dacha/zdorove/optika',
'dom-i-dacha/zdorove/ortopediya',
'zdorove/meditsinskie-izdeliya-i-pribory/sredstva-reabilitatsii',
'zdorove/uhod-za-polostyu-rta'],
'Ремонт':
['dlya-remonta/dveri-okna-i-furnitura',
'dom-i-dacha/instrumenty/instrumenty',
'dom-i-dacha/tovary-dlya-remonta/otdelochnye-materialy',
'bytovaya-tehnika/stroitelstvo-i-remont/elektrika',
'dlya-remonta/lakokrasochnye-materialy',
'dlya-remonta/santehnika-otoplenie-i-gazosnabzhenie',
'dlya-remonta/ventilyatsiya',
'dlya-remonta/krepezh',
'dlya-remonta/stroymaterialy',
'dom-i-dacha/vannaya',
'dom-i-dacha/kuhnya',
'dlya-doma/predmety-interera',
'dom/spalnya',
'dom/gostinnaya',
'dom/detskaya',
'dom/dosug-i-tvorchestvo',
'dom/zerkala',
'dlya-doma/mebel/kronshteiny',
'dom/osveshchenie',
'dom/dlya-kureniya',
'dom-i-dacha/otdyh-na-prirode',
'dom/mebel',
'dom/prihozhaya',
'dlya-doma/predmety-religii',
'dlya-doma/bytovaya-himiya/bytovaya-himiya',
'dom/hranenie-veshchey',
'dom/shtory'],
'Автотовары':
['avtotovary/zapchasti-na-gruzovye-avtomobili',
'avtotovary/masla-i-zhidkosti',
'aksessuary/avtotovary/uhod-za-avtomobilem',
'aksessuary/avtotovary/avtoaksessuary-i-dopolnitelnoe-oborudovanie',
'avtotovary/shiny-i-diski',
'avtotovary/instrumenty',
'avtotovary/mototovary'],
'Ювелирные':
['yuvelirnye-ukrasheniya/koltsa',
'yuvelirnye-ukrasheniya/sergi',
'yuvelirnye-ukrasheniya/braslety',
'yuvelirnye-izdeliya/podveski-i-sharmy',
'yuvelirnye-izdeliya/komplekty',
'yuvelirnye-izdeliya/tsepi-i-shnurki',
'yuvelirnye-ukrasheniya/broshi',
'yuvelirnye-ukrasheniya/pirsing',
'yuvelirnye-ukrasheniya/chasy',
'yuvelirnye-izdeliya/zazhimy-i-zaponki',
'yuvelirnye-ukrasheniya/chetki',
'yuvelirnye-izdeliya/suveniry-i-stolovoe-serebro',
'yuvelirnye-ukrasheniya/zoloto',
'yuvelirnye-ukrasheniya/serebro',
'yuvelirnye-ukrasheniya/ukrasheniya-iz-keramiki',
'yuvelirnye-izdeliya/aksessuary-dlya-ukrasheniy']}

url_category_list={}
#Проверяем ссылки и добавляем в список
for t in tqdm(list(categories.keys())):
    url_list=[]
    for i in tqdm(categories[t]):
        time.sleep(1)
        w=1
        url = str('https://www.wildberries.ru/catalog/'+i)
        while w>0:
            if w>200:
                print(url)
                break
            try:
                response = requests.get(url, headers=headers, params=None) 
                html = response.text
                soup = BeautifulSoup(html, 'lxml')
                good_count = soup.find('span', class_='goods-count').get_text(strip=True).replace("\xa0", '').split()[0]
                url_list.append(url)
                w=(-10)
            except:
                w+=1
    url_category_list[t]=url_list
i=0
url=0

In [11]:
i=0
count_of_page=3 # число первых n страниц популярных товаров каждой категории
category_cards={}
sum_cards=0
# создаем список ссылок на товары
for t in tqdm(list(url_category_list.keys())):
    cards=[]
    for q in tqdm(url_category_list[t]):
        pages = get_pages(q)
        if pages > count_of_page:
            pages = count_of_page
        else:
            pages = pages
        for page in range(1, pages+1):
            time.sleep(1)
            b=1
            while b>0:
                try:
                    previous = len(cards)
                    html = (requests.get(q, headers=headers, params={'sort': 'popular','page': page})).text
                    soup = BeautifulSoup(html, 'html.parser') 
                    items = soup.find_all('div', class_="product-card") 
                    for item in items: 
                        cards.append(f'https://www.wildberries.ru{item.find("a", class_="product-card__main").get("href")}')
                    if len(cards)>previous:
                        b=-10
                except:
                    b+=1
    print(t + ': ' + str(len(cards)))
    sum_cards+=int(len(cards))
    print(sum_cards)
    category_cards[t]=cards
b=0


Женщинам: 3958
3958



Мужчинам: 3447
7405



Детям: 3335
10740



Обувь: 1816
12556



Аксессуары: 6060
18616


...


Дача: 4536
58459



Здоровье: 3649
62108



Ремонт: 8185
70293



Автотовары: 2113
72406



Ювелирные: 4433
76839



In [12]:
#раскидать на ячейки для контроля обработки данных
max_list = 500
category_cards_list={}
for t in tqdm(list(category_cards.keys())):
    cards_list=[]
    z = 0
    list_of_cards = []
    for n in category_cards[t]:
        if z < max_list:
            list_of_cards.append(n)
            print(len(list_of_cards))
        else:
            cards_list.append(list_of_cards)
            print('Сформировано {} ячеек!'.format(len(cards_list)))
            z=0
            list_of_cards = []
            list_of_cards.append(n)
            print(len(list_of_cards))
        z+=1
    if len(list_of_cards)>0:
        cards_list.append(list_of_cards)
        print('ИТОГО: {} ячеек!'.format(len(cards_list)))
    category_cards_list[t]=cards_list

#сохраняем все это на внешний репозиторий
with open('base.txt', 'w') as f:
    f.write(str(category_cards_list))

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
353
354
355
356
357
358
359
360
361
362
363
364
365
366
367
368
369
370
371
372
373
374
375
376
377
378
379
380
381
382
383
384
385
386
387
388
389
390
391
392
393


224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
353
354
355
356
357
358
359
360
361
362
363
364
365
366
367
368
369
370
371
372
373
374
375
376
377
378
379
380
381
382
383
384
385
386
387
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
405
406
407
408
409
410
411
412
413
414
415
416
417
418
419
420
421
422
423
424
425
426
427
428
429
430
431
432
433
434
435
436
437
438
439
440
441
442
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461
462
463
464
465
466
467
468
469
470
471
472
473


294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
ИТОГО: 7 ячеек!
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231


182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
353
354
355
356
357
358
359
360
361
362
363
364
365
366
367
368
369
370
371
372
373
374
375
376
377
378
379
380
381
382
383
384
385
386
387
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
405
406
407
408
409
410
411
412
413
414
415
416
417
418
419
420
421
422
423
424
425
426
427
428
429
430
431


...

33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
ИТОГО: 8 ячеек!
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173

376
377
378
379
380
381
382
383
384
385
386
387
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
405
406
407
408
409
410
411
412
413
414
415
416
417
418
419
420
421
422
423
424
425
426
427
428
429
430
431
432
433
434
435
436
437
438
439
440
441
442
443
444
445
446
447
448
449
450
451
452
453
454
455
456
457
458
459
460
461
462
463
464
465
466
467
468
469
470
471
472
473
474
475
476
477
478
479
480
481
482
483
484
485
486
487
488
489
490
491
492
493
494
495
496
497
498
499
500
Сформировано 6 ячеек!
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
14

126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
353
354
355
356
357
358
359
360
361
362
363
364
365
366
367
368
369
370
371
372
373
374
375


175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343
344
345
346
347
348
349
350
351
352
353
354
355
356
357
358
359
360
361
362
363
364
365
366
367
368
369
370
371
372
373
374
375
376
377
378
379
380
381
382
383
384
385
386
387
388
389
390
391
392
393
394
395
396
397
398
399
400
401
402
403
404
405
406
407
408
409
410
411
412
413
414
415
416
417
418
419
420
421
422
423
424


53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314

In [3]:
# основная фнкция парсинга данных с ссылки на продукт
def product_card_get(item):
    timer = 0
    product_card=[]
    response = requests.get(item, headers=headers, params=None) 
    html = response.text
    soup = BeautifulSoup(html, 'lxml')
    js_scripts = soup.find_all('script')
    m = re.search('ssrModel: (.+),', str(js_scripts))
    while m == None:
        if timer<7:
            time.sleep(timer)
            response = requests.get(item, headers=headers, params=None) 
            html = response.text
            soup = BeautifulSoup(html, 'lxml')
            js_scripts = soup.find_all('script')
            m = re.search('ssrModel: (.+),', str(js_scripts))
            timer+=0.5
        else:
            print(item)
            break
    if m!=None:
        data = json.loads(m.group(1))
        product_id = data['product']['nomenclatures'][0]['nmId']
        if int(soup.find('span', class_='same-part-kt__count-review').get_text(strip=True).replace("\xa0", '').split()[0])!=0:
            d=1
            g=20
            while d>=0:
                try: 
                    response = (requests.get('https://napi.wildberries.ru/api/catalog/{}/detail.aspx'.format(product_id), headers=headers, params=None))
                    html = response.text
                    soup2 = BeautifulSoup(html, 'lxml')
                    js_scripts = soup2.find_all('p')
                    m = str(js_scripts)[4:-5]
                    data2 = json.loads(m)
                    try:
                        if data2['data']['errorMsg']=='Товар не найден':
                            if g>=0:
                                date=0
                                g-=1
                            if g<=1:
                                date=0
                                d=-100
                    except:
                        response = (requests.get('https://napi.wildberries.ru/api/product/feedback/{}?page=1&order=Asc&field=Date'.format(data2['data']['productInfo']['imt']), headers=headers, params=None))
                        html = response.text
                        html=html.replace('<','none')
                        soup3 = BeautifulSoup(html, 'lxml')
                        js_scripts = soup3.find_all('p')
                        m = str(js_scripts)[4:-5].replace('</led_profi>','')
                        data3 = json.loads(m)
                        try:
                            if data3['data']['feedback']==[]:
                                print('ok')
                                if g>=0:
                                    date=0
                                    g-=1
                                if g<0:
                                    date=0
                                    d=-100
                            else:
                                date = data3['data']['feedback'][0]['date'][:-6].replace(',','').replace('Вчера',(datetime.now()-timedelta(days=1)).strftime("%d %m")).replace('Сегодня',datetime.now().strftime("%d %m")).split(' ')
                                d=-100
                        except:
                            try:
                                date = data3['data']['feedback'][0]['date'][:-6].replace(',','').replace('Вчера',(datetime.now()-timedelta(days=1)).strftime("%d %m")).replace('Сегодня',datetime.now().strftime("%d %m")).split(' ')
                                d=-100
                            except:
                                d+=1
                except:
                    d+=1
            if d>100:
                date=0
                print("Пропустил!")
                print('https://napi.wildberries.ru/api/product/feedback/{}?page=1&order=Asc&field=Date'.format(data2['data']['productInfo']['imt']))   
            if date!=0:
                if len(date)<3:
                    date.append(str(datetime.now().year))
                month=0
                for i in ['января','февраля','марта','апреля','мая','июня','июля','августа','сентября','октября','ноября','декабря']:
                    month+=1
                    if date[1]==i:
                        date[1]=str(month)
                date=str(date[0]+'-'+date[1]+'-'+date[2])
                date=datetime.strptime(date, '%d-%m-%Y')
        else:
            date=0
        i = 0
        while i>(-1):
            if i > 10:
                price = 0
                break
            try: 
                price = data['product']['nomenclatures'][i]['price']['price']
                break
            except:
                i+=1
        if price !=0:
            try: 
                sales = data['product']['nomenclatures'][0]['price']['sale']
            except:
                sales = data['product']['nomenclatures'][1]['price']['sale']
        else:
            sales = 0 
        try: 
            typer = data['sitePath'][0]['name']
        except:
            typer = 0
        if date==0:
            print(item)
        product_card.append([
        data['product']['goodsName'],
        typer,
        data['product']['brandName'],
        data['product']['star'],
        data['product']['nomenclatures'][0]['ordersCount'],
        price,
        sales,
        price*(100-(sales))/100,
        int(soup.find('span', class_='same-part-kt__count-review').get_text(strip=True).replace("\xa0", '').split()[0]),
        data['product']['adult'],
        date,
        item]
        )
        return product_card

In [70]:
#восстанавливаем базу ссылок из внешнего репозитория
file = open("base.txt", "r")
contents = file.read()
category_cards_list = ast.literal_eval(contents)
file.close()



#выбираем тут категорию товаров!!!!!!
no=6



t=list(category_cards_list.keys())[no]
print('Выбрана категория {}:'.format(no), t)
print('Всего категорий:', len(category_cards_list)-1)

Выбрана категория 6: Книги
Всего категорий: 15


In [74]:
#время ожидания между запросами для избежания блокировки

c=13
optimizator = 5

while c < len(category_cards_list):
    no=c
    t=list(category_cards_list.keys())[no]
    print('Выбрана категория {}:'.format(no), t)
    turn = optimizator
    file=[]

    #Выгрузка данных
    for s in tqdm(category_cards_list[t]):
        for i in tqdm(s):
            if turn < 1:
                turn = optimizator
                time.sleep(optimizator-1)
            file.append(product_card_get(i))
            turn -= 1
        print(len(file))
    
    #сохранение в резервную переменную
    exec("file_reserv_{} = file".format(no))
    
    #сохранение категории в резервный файл. Выбор категории.

    exec("file = file_reserv_{}".format(no))
    file_todf=[]
    i=0
    
    while i < int(len(file)):
        print(file[i])  
        if file[i]!=None:  
            file_todf+=file[i]
        i+=1
    file_df = pd.DataFrame(file_todf, columns=['Наименование','Тип', 'Бренд', 'Рейтинг', 'Заказов', 'Цена', 'Скидка', 'Цена продажи', 'Комментариев', '18+', 'Начало продаж', 'URL товара'])
    
    file_df = pd.DataFrame(file_todf, columns=['Наименование','Тип', 'Бренд', 'Рейтинг', 'Заказов', 'Цена', 'Скидка', 'Цена продажи', 'Комментариев', '18+', 'Начало продаж', 'URL товара'])
    file_df['Начало продаж'].replace(0, np.nan, inplace = True)
    
    file_df.dropna(inplace=True)
    file_df.drop_duplicates(inplace=True)
    
    now=datetime.now()
    file_df['Месяцев продается'] = ((now - file_df['Начало продаж']).dt.days)/30
    file_df['Среднемесячные продажи'] = (file_df['Заказов']/file_df['Месяцев продается'])
    file_df['Среднемесячная выручка']=(file_df['Цена продажи']*file_df['Среднемесячные продажи']).fillna(0)
    file_df['Бюджет на месяц']=((file_df['Цена продажи']+file_df['Цена'])/2*file_df['Среднемесячные продажи']*1/2).fillna(0)
    file_df['Чистая прибыль в месяц']=(file_df['Среднемесячная выручка']-file_df['Бюджет на месяц']).fillna(0)
    file_df
    
    exec("file_{} = file_df".format(no))
    print('Сформирован ' + "file_{}".format(no))
    var="file_{}".format(no)
    
    file_df.to_csv("file_{}.csv".format(no), sep='\t', encoding='cp1251', index = False, header=True)
    c+=1



Выбрана категория 13: Ремонт


  0%|          | 0/17 [00:00<?, ?it/s]

  0%|          | 0/500 [00:00<?, ?it/s]

https://www.wildberries.ru/catalog/51885935/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/46663434/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/41698418/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/39350023/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/51885935/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/39350056/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/38751495/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/38731842/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/48677502/detail.aspx?targetUrl=GP
500


  0%|          | 0/500 [00:00<?, ?it/s]

...

  0%|          | 0/433 [00:00<?, ?it/s]

https://www.wildberries.ru/catalog/49634893/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/29512387/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/44843590/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/37659029/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/44843585/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/29509191/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/51957438/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/29301006/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/32328299/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/44843556/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/53571626/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/31419217/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/29511601/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/35875726/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog

https://www.wildberries.ru/catalog/29652589/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/16508546/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/44286406/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/46937210/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/9356170/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/54444649/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/50237311/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/51804247/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/30970191/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/40694827/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/39374348/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/28237424/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/16009482/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/44842927/detail.aspx?targetUrl=GP
https://www.wildberries.ru/catalog/

[['Ювелирные запонки', 'Ювелирные изделия', 'SOKOLOV', 5, 50, 0, 0, 0.0, 4, False, datetime.datetime(2021, 4, 14, 0, 0), 'https://www.wildberries.ru/catalog/22907192/detail.aspx?targetUrl=GP']]
[['Серебряный замок Эльф Санты/с натуральным зелёным ониксом/подарок/коллекционный', 'Ювелирные изделия', 'Trollbeads', 5, 1, 6300, 0, 6300.0, 1, False, datetime.datetime(2022, 1, 5, 0, 0), 'https://www.wildberries.ru/catalog/51893732/detail.aspx?targetUrl=GP']]
[['Зажим для галстука комплектом с запонками', 'Ювелирные изделия', 'SILVERMEN', 5, 100, 5850, 17, 4855.5, 3, False, datetime.datetime(2019, 8, 28, 0, 0), 'https://www.wildberries.ru/catalog/8804653/detail.aspx?targetUrl=GP']]
[['Ювелирный подарочный комплект в футляре: зажим для галстука, запонки', 'Ювелирные изделия', 'SILVERMEN', 5, 100, 3910, 22, 3049.8, 4, False, datetime.datetime(2019, 10, 1, 0, 0), 'https://www.wildberries.ru/catalog/7569932/detail.aspx?targetUrl=GP']]
[['Запонки комплектом/с зажимом/в подарок', 'Ювелирные изделия

Сформирован file_15


In [19]:
df = []
for i in range (0,16):
    exec("df_time = pd.read_csv('file_{}.csv', sep='\t', encoding='cp1251')".format(i))
    df.append(df_time)
result = pd.concat(df, join="outer", ignore_index=True)
result.dropna(inplace=True)
result.drop_duplicates(inplace=True, ignore_index=True)
i=0
while i <+ int(len(result['Среднемесячная выручка'])):
    result['Среднемесячная выручка'][i]="%.2f" % result['Среднемесячная выручка'][i]
    result['Бюджет на месяц'][i]="%.2f" % result['Бюджет на месяц'][i]
    result['Месяцев продается'][i]="%.1f" % result['Месяцев продается'][i]
    result['Среднемесячные продажи'][i]=result['Среднемесячные продажи'][i].astype(int)
    result['Чистая прибыль в месяц'][i]="%.2f" % result['Чистая прибыль в месяц'][i]
    i+=1
result.to_csv("result.csv", sep='\t', encoding='cp1251', index = False, header=True)

C:\Users\nevge\AppData\Local\Temp/ipykernel_10184/2949332975.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['Среднемесячная выручка'][i]="%.2f" % result['Среднемесячная выручка'][i]
C:\Users\nevge\AppData\Local\Temp/ipykernel_10184/2949332975.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  result['Бюджет на месяц'][i]="%.2f" % result['Бюджет на месяц'][i]
C:\Users\nevge\AppData\Local\Temp/ipykernel_10184/2949332975.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gu

In [20]:
result.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 64364 entries, 0 to 64363
Data columns (total 17 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   Наименование            64364 non-null  object 
 1   Тип                     64364 non-null  object 
 2   Бренд                   64364 non-null  object 
 3   Рейтинг                 64364 non-null  int64  
 4   Заказов                 64364 non-null  int64  
 5   Цена                    64364 non-null  int64  
 6   Скидка                  64364 non-null  int64  
 7   Цена продажи            64364 non-null  float64
 8   Комментариев            64364 non-null  int64  
 9   18+                     64364 non-null  bool   
 10  Начало продаж           64364 non-null  object 
 11  URL товара              64364 non-null  object 
 12  Месяцев продается       64364 non-null  float64
 13  Среднемесячные продажи  64364 non-null  float64
 14  Среднемесячная выручка  64364 non-null

In [21]:
result = pd.read_csv("result.csv", sep='\t', encoding='cp1251')
Strategy = result[(result['Месяцев продается'] >= 3) & 
                   (result['18+'] == False)].sort_values(by='Среднемесячные продажи', ascending=False).head(100)
pd.set_option('display.max_rows', None)
Strategy

Наименование              Тип  \
34500  Маска от черных точек Lanbena очищающая поры/о...                0   
42487  Натуральная пастила без сахара, ассорти 0,8 кг...         Продукты   
2820   Маска от черных точек Lanbena очищающая поры/о...                0   
34496  Маска от черных точек Lanbena очищающая поры/о...                0   
50808  Перчатки одноразовые\nНитриловые\nМедицинские\...         Женщинам   
21301  ОГЭ-2022 Математика: типовые экзаменационные в...            Книги   
29360  Средство для педикюра Гель для пяток с мочевин...          Красота   
32275  Гель для бровей и ресниц "FIX&CARE", 4,3 мл , ...          Красота   
45125  Натуральное сушеное манго без сахара/King Frui...         Продукты   
15939  Беспроводные наушники Dsaila A2 с анимацией / ...      Электроника   
18568  Беспроводные наушники Dsaila A2 с анимацией / ...      Электроника   
58957  Finish All in1 Max Таблетки для посудомоечной ...              Дом   
34491  Средство для педикюра Гель для пяток с мочевин...          Красота   
59033  Пятновыводитель-отбеливатель, гипоаллергенный,...              Дом   
15962  Наушники с анимацией/Беспроводные i12 Bluetoot...      Электроника   
18603  Наушники с анимацией/Беспроводные i12 Bluetoot...      Электроника   
32250  Гель для бровей суперсильной фиксации BROW SUP...          Красота   
32252  Тушь для ресниц удлиняющая "Lash Sensational. ...                0   
33774  Средство для педикюра Гель для пяток с мочевин...          Красота   
29343  Средство для педикюра Гель для пяток с мочевин...          Красота   
33828  Средство для педикюра Гель для пяток с мочевин...          Красота   
43370  Коллаген для суставов/порошок с витамином с/До...         Продукты   
33789  Ресницы, для бровей, для роста ресниц и бровей...                0   
34520  Ресницы, для бровей, для роста ресниц и бровей...                0   
58969                  Таблетки для посудомоечной машины              Дом   
3127   Футболка прикол / мем / Новогодний подарок / Н...         Мужчинам   
20602     Весы кухонные электронные/Настольные для кухни  Бытовая техника   
29367  Пилки для ногтей абразив 100 180 и 180 240 наб...          Красота   
29661  Шампунь + Бальзам-архитектор без сульфатов и п...                0   
3191   Футболка Пивозавр/ утро добрым не бывает подар...         Мужчинам   
58988                                 Стиральный порошок              Дом   
42486  Белёвская пастила фруктовая ассорти 800г БЕЗ С...         Продукты   
29645  Спрей для мгновенного восстановления 17 в 1. Д...                0   
33771  Спрей для мгновенного восстановления 17 в 1. Д...                0   
3973   Трусы мужские боксеры однотонные, без принта н...         Мужчинам   
32264  Тушь для ресниц со сценическим эффектом (супер...                0   
21303  ОГЭ-2022 Обществознание: типовые экзаменационн...            Книги   
5756   Леггинсы утепленные детские / тёплые леггинсы ...            Детям   
33782  Набор для депиляции воском/Воскоплав/Воск горя...          Красота   
32272  Гель для бровей и ресниц фиксирующий Fixateur ...          Красота   
29958  Средство для гигиенического ухода за сосками, ...                0   
32265  Тушь для ресниц XXL Суперобъем, Эффект накладн...                0   
58963  Гель для стирки универсальный, концентрат, гип...              Дом   
32297                                   Карандаш для губ                0   
20542        Помпа для воды/для электрическая/для кулера  Бытовая техника   
50830                               Перчатки одноразовые         Женщинам   
15944  Светящиеся детские беспроводные наушники с ушк...      Электроника   
18570  Светящиеся детские беспроводные наушники с ушк...      Электроника   
33975                          Kotex Ночные трусики 2шт.          Красота   
33965        Влажные салфетки Elite Soft, (56x3) 168 шт.          Красота   
34594  Крем от псориаза, мазь от псориаза, мазь от эк...                0   
29385     Пилка для ногтей для маникюра,

<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"></ul></div>